# Numerical simulatin of β-catenin destruction cycle

(c) 2018 Justin Bois. This work is licensed under a [Creative Commons Attribution License CC-BY 4.0](https://creativecommons.org/licenses/by/4.0/). All code contained herein is licensed under an [MIT license](https://opensource.org/licenses/MIT).

*This document was generated from a Jupyter notebook, which may be downloaded [here](l03_betacat_destruction_cycle.ipynb).*

In [1]:
import numpy as np
import scipy.integrate

import bokeh.models
import bokeh.plotting
import bokeh.io
bokeh.io.output_notebook()

Loading BokehJS ...

We first set up the parameters.  Most are measured and reported, at least approximately, in the Lee, et al. paper.  The parameters $k_8$, $k_{\text{-}8}$ and $k_{12}$ are unknown.  However, $K_\mathrm{d} = k_{\text{-}8}/k_8$ is known, so we only have two parameters to set.

In [15]:
# Key for names
names = ['Axin complex', 'Axin-βcat', 'Axin-βcat*', 'βcat*', 'βcat']

# Define known parameters
c_A = 50          # nM (given by fixed GSK-3 concentration)
k9 = 206          # 1/min
k10 = 206         # 1/min
k11 = 0.417       # 1/min
Kd8 = 120         # nM

# Unknown parameters
km8 = 1          # 1/min
k12 = 100         # nM/min

# k8 determined form Kd8 and km8
k8 = km8 / Kd8    # 1/nM-min

# Set up params for ODE
params = np.array([k8, km8, k9, k10, k11, k12])

For our initial conditions, we will assume that we have no $\beta$-catenin and that we have a fixed amount of APC/Axin/GKC-3.

In [16]:
# Initial conditions
c0 = np.array([c_A, 0, 0, 0, 0])

Now we define the time derivative.  We use the functional form that is necessary to pass into `scipy.integrate.odeint()`.

In [17]:
def dcdt(c, t, k8, km8, k9, k10, k11, k12):
    """
    Time derivative of concentrations.
    c = (c3, c8, c9, c10, c11)
    """
    # Unpack concentrations
    c3, c8, c9, c10, c11 = c
    
    # Build derivatives
    deriv = np.empty(5)
    deriv[0] = -k8*c3*c11 + km8*c8 + k10*c9
    deriv[1] = k8*c3*c11 - (km8 + k9)*c8
    deriv[2] = k9*c8 - k10*c9
    deriv[3] = k10*c9 - k11*c10
    deriv[4] = -k8*c3*c11 + km8*c8 + k12
    
    return deriv

Now, we just have to specify what time points we want and then run the solver!

In [18]:
# Set up time points and solve
t = np.linspace(0, 20, 300)
c = scipy.integrate.odeint(dcdt, c0, t, args=(k8, km8, k9, k10, k11, k12))

Finally, we can plot the solution.

In [19]:
# Set up canvas on which to paint plot
p = bokeh.plotting.figure(plot_width=650,
                          plot_height=400,
                          x_axis_label='time (min)',
                          y_axis_label='conc (nM)',
                          border_fill_alpha=0,
                          background_fill_alpha=0)

# Specify colors
colors = bokeh.palettes.d3['Category10'][10]

# Add glyphs
for i, name in enumerate(names):
    p.line(t, c[:,i], line_width=3, color=colors[i], legend=name)

# Place legend
p.legend.location = 'center_right'

bokeh.io.show(p)

The Axin complexes almost immediately go to steady state, and then the β-catenin levels respond more slowly as they reach their steady state.